In [ ]:
def polygonGenerator(image,hullMode):
    import scipy
    from scipy.spatial import ConvexHull, convex_hull_plot_2d
    import numpy as np
    import matplotlib.pyplot as plt
    from shapely import geometry
    from descartes import PolygonPatch
    
    
    #Get coordinates where road was detected
    coords = np.column_stack(np.where((image)==1))

    #Convert the image to grayscale & find edges
    img = np.uint8(np.float32(image))
    edges = cv2.Canny(img,3,3)

    
    #fig, ax = plt.subplots(figsize=(30, 30))
    #plt.subplot(121),plt.imshow(img,cmap = 'gray')
    #plt.title('Original Image'), plt.xticks([]), plt.yticks([])
    #plt.subplot(122),plt.imshow(edges,cmap = 'gray')
    #plt.title('Edge Image'), plt.xticks([]), plt.yticks([])
    #plt.show()
    
    #select the coordinates where the edges where found and define [0,0] as point to close the loop
    coords = np.column_stack(np.where(edges==255))
    points = np.zeros((len(coords)+1, 2))
    points[:len(coords),:]= coords
    points[len(coords),0]= 736
    points[:,0]=720-points[:,0]     # change the axis 


    #plt.plot(points[:,1], points[:,0], 'ro')
    #plt.show()

    if hullMode ==True:
    #Define the hull that best fit the points
        hull= ConvexHull(points)

        fig, ax = plt.subplots(figsize=(15, 15))
        ax.set_title('Convex Hull')
        ax.imshow(image)
        ax.set_axis_off()  
        ax.plot(points[hull.vertices,1], 720-points[hull.vertices,0], 'w-', lw=2)
        ax.plot(points[hull.vertices[:],1], 720-points[hull.vertices[:],0], 'ro')

        pointList=[]
        for i in range(len(hull.vertices[:])):
            p = geometry.Point(points[hull.vertices[i],1],points[hull.vertices[i],0])
            pointList.append(p)
            


        poly = geometry.Polygon([[p.x, p.y] for p in pointList])
        x,y = poly.exterior.xy
        ring_patch = PolygonPatch(poly)
        
        fig, ay = plt.subplots(figsize=(15, 15))
        ay.add_patch(ring_patch)
        ay.set_title('Filled Polygon')
        xrange = [0, 1300]
        yrange = [-20, 800]
        ay.set_xlim(*xrange)
        ay.set_ylim(*yrange)
        ay.set_aspect(1)
        ay.set_axis_off()  
    else:
        points = np.column_stack(np.where((image)==1))
        fig, ax = plt.subplots(figsize=(15, 15))
        ax.imshow(image)
        ax.set_axis_off()
        ax.plot(points[:,1],720-points[:,0], 'o')    

    return points

def polygonStitcher(Points,img_height,img_width,M_left_center,M_center_right,result_width):
    import cv2
    import numpy as np
    
    (PointsE, PointsM, PointsD) = Points
    
    pointsE[:,0]= img_height-pointsE[:,0]
    pointsM[:,0]= img_height-pointsM[:,0]
    pointsD[:,0]= img_height-pointsD[:,0]
    
    
    pointsD[:,[0, 1]] = pointsD[:,[1, 0]]
    pointsM[:,[0, 1]] = pointsM[:,[1, 0]]
    pointsE[:,[0, 1]] = pointsE[:,[1, 0]]
    d = np.array([pointsD.astype('float32')])
    m = np.array([pointsM.astype('float32')])
    e = np.array([pointsE.astype('float32')])

    T = np.array([[1.0, 0.0, (result_width/2)-(img_width/2)],
                          [0.0, 1.0, 0.0],
                          [0.0, 0.0, 1.0]]).astype(dtype=np.float32)


    pointsOutD = cv2.perspectiveTransform(d, np.dot(T,M_center_right))
    pointsOutM = cv2.perspectiveTransform(m, T)
    pointsOutE = cv2.perspectiveTransform(e, np.dot(T,M_left_center))
    
    pointsOutE = pointsOutE[-1,:,:]
    pointsOutM = pointsOutM[-1,:,:]
    pointsOutD = pointsOutD[-1,:,:]
    
    imagemPoints = np.zeros([img_height,result_width])
    
    fig, ax = plt.subplots(figsize=(15, 15))
    ax.imshow(imagemPoints,cmap='gray')
    ax.plot(pointsOutE[:,0], pointsOutE[:,1], 'wo')
    ax.plot(pointsOutD[:,0], pointsOutD[:,1], 'wo')
    ax.plot(pointsOutM[:,0], pointsOutM[:,1], 'wo')
    xrange = [0, 3000]
    yrange = [0, 736]
    ax.set_xlim(*xrange)
    ax.set_ylim(*yrange)
    ax.set_aspect(1)
    ax.set_axis_off()
    
    return 
    